## **Big Data Project**: *NCAA Basketball*

[source](https://console.cloud.google.com/marketplace/product/ncaa-bb-public/ncaa-basketball?q=search&referrer=search&project=big-data-sports)

 | Table | Description |
 | ----------- | ----------- |
 | **mbb_games_sr** | Team-level box scores from every men's basketball game from the 2013-14 season to the 2017-18 season. Each row shows both teams' stats for that one game. Data provided by Sportradar LLC, see www.sportradar.com for more details. |
 | **mbb_players_games_sr** | Player-level box scores from every men's basketball game from the 2013-14 season to the 2017-18 season. Each row shows a single player's stats in one game. Data provided by Sportradar LLC, see www.sportradar.com for more details. |

---
---

In [43]:
import dask
import dask.dataframe as dd
from dask.distributed import Client, progress
import dask.array as da
from dask.diagnostics import Profiler, ResourceProfiler, CacheProfiler
import timeit

import pandas as pd
import numpy as np

#prefs
pd.set_option('max_columns', None)

### *Setting up a new dask connection*
---

In [44]:
#close existing dask connection if it exists and open a new one
try:
    if client is not None:
        client.close()
        print("closed existing connection, ",client)       
except Exception as e:
    print(e)
    

closed existing connection,  <Client: not connected>


In [45]:
#get new connection
client = Client(n_workers=2, threads_per_worker=2, memory_limit='8GB')
display(client)

<Client: 'tcp://127.0.0.1:59726' processes=2 threads=4, memory=14.90 GiB>

In [53]:
# first, pip install gcsfs
# games_data = dd.read_csv('gcs://sportsdata641/Datasets/mbb_games_sr')
games_data = dd.read_csv('gcs://sportsdata641/Datasets/mbb_games_sr', dtype={'a_assists': 'float64', 'a_blocked_att': 'float64','a_blocks': 'float64',\
                                                                             'a_coach_tech_fouls': 'float64','a_defensive_rebounds': 'float64',\
                                                                             'a_ejections': 'float64','a_field_goals_att': 'float64','a_field_goals_made': 'float64',\
                                                                             'a_flagrant_fouls': 'float64','a_free_throws_att': 'float64',\
                                                                             'a_free_throws_made': 'float64','a_offensive_rebounds': 'float64',\
                                                                             'a_personal_fouls': 'float64','a_player_tech_fouls': 'float64',\
                                                                             'a_points': 'float64','a_rebounds': 'float64',\
                                                                             'a_steals': 'float64','a_team_rebounds': 'float64','a_team_tech_fouls': 'float64',\
                                                                             'a_team_turnovers': 'float64','a_three_points_att': 'float64',\
                                                                             'a_three_points_made': 'float64','a_turnovers': 'float64','a_two_points_att': 'float64',\
                                                                             'a_two_points_made': 'float64','attendance': 'float64','h_assists': 'float64',\
                                                                             'h_blocked_att': 'float64','h_blocks': 'float64','h_coach_tech_fouls': 'float64',\
                                                                             'h_defensive_rebounds': 'float64','h_ejections': 'float64',\
                                                                             'h_field_goals_att': 'float64','h_field_goals_made': 'float64',\
                                                                             'h_flagrant_fouls': 'float64','h_free_throws_att': 'float64',\
                                                                             'h_free_throws_made': 'float64','h_offensive_rebounds': 'float64',\
                                                                             'h_personal_fouls': 'float64','h_player_tech_fouls': 'float64','h_points': 'float64',\
                                                                             'h_rebounds': 'float64','h_steals': 'float64','h_team_rebounds': 'float64',\
                                                                             'h_team_tech_fouls': 'float64','h_team_turnovers': 'float64',\
                                                                             'h_three_points_att': 'float64','h_three_points_made': 'float64',\
                                                                             'h_turnovers': 'float64','h_two_points_att': 'float64','h_two_points_made': 'float64',\
                                                                             'periods': 'float64','venue_capacity': 'float64','venue_zip': 'object'})

# Aggregating Play-by-play data for first half

In [5]:
pbp_data = dd.read_csv('gcs://sportsdata641/Datasets/mbb_pbp_sr*', usecols =['period','game_id','team_id','home_id','away_id','event_type','event_description'],\
                      dtype={'team_id':object})

In [6]:
#Filtering out non-team events (e.g., official timeouts) and events from the second half
pbp_data2=pbp_data[(pbp_data["team_id"].notnull())&(pbp_data["period"]==1)]

In [7]:
pbp_data2.head()

game_id  \
19141  063879c7-2bae-473f-aa3f-8a68f444bb73   
19142  063879c7-2bae-473f-aa3f-8a68f444bb73   
19143  063879c7-2bae-473f-aa3f-8a68f444bb73   
19145  063879c7-2bae-473f-aa3f-8a68f444bb73   
19150  063879c7-2bae-473f-aa3f-8a68f444bb73   

                                    away_id  \
19141  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19142  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19143  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19145  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19150  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   

                                    home_id  period  \
19141  532d3874-b4b3-4c5c-acc6-749a6db26c8f       1   
19142  532d3874-b4b3-4c5c-acc6-749a6db26c8f       1   
19143  532d3874-b4b3-4c5c-acc6-749a6db26c8f       1   
19145  532d3874-b4b3-4c5c-acc6-749a6db26c8f       1   
19150  532d3874-b4b3-4c5c-acc6-749a6db26c8f       1   

                                    team_id  \
19141  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19142  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19143  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19145  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19150  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   

                           event_description     event_type  
19141      Omar Richard turnover (traveling)       turnover  
19142  Omar Richard misses free throw 1 of 2  freethrowmiss  
19143    Jay Mayernik misses two point layup   twopointmiss  
19145     Jay Mayernik makes two point layup   twopointmade  
19150    Javonte Byrd misses two point layup   twopointmiss

In [8]:
#pbp_data2.compute()
#1852059 rows is about 10k+ games, assuming about 170 first half plays per game

Note: event_type definitions can be found here: https://developer.sportradar.com/docs/basketball/NCAA_Mens_Basketball_v7#frequently-asked-questions

In [9]:
pbp_data2["2PA"]=(pbp_data2["event_type"].isin(["twopointmade","twopointmiss"]))
pbp_data2["2PM"]=(pbp_data2["event_type"]=="twopointmade")
pbp_data2["3PA"]=(pbp_data2["event_type"]=="threepointmade")|(pbp_data2["event_type"]=="threepointmiss")
pbp_data2["3PM"]=(pbp_data2["event_type"]=="threepointmade")
pbp_data2["FTA"]=(pbp_data2["event_type"]=="freethrowmade")|(pbp_data2["event_type"]=="freethrowmiss")
pbp_data2["FTM"]=(pbp_data2["event_type"]=="freethrowmade")
pbp_data2["TRB"]=(pbp_data2["event_type"]=="rebound")
pbp_data2["TO"]=(pbp_data2["event_type"]=="turnover")
pbp_data2["Foul"]=(pbp_data2["event_type"].isin(["flagrantone","flagranttwo","clearpathfoul","technicalfoul",\
                                                "minortechnicalfoul","personalfoul","defensivethreeseconds"]))
pbp_data2["Flagrant"]=(pbp_data2["event_type"].isin(["flagrantone","flagranttwo"]))
pbp_data2["Ejection"]=(pbp_data2["event_type"]=="ejection")


In [10]:
#pbp_data2.compute()

In [11]:
def checkast(row):
    if row["event_type"] in ["twopointmade","threepointmade"]:
        return "assist" in row["event_description"]
    else:
        return False


pbp_data2["AST"] =pbp_data2.apply(checkast,axis=1)

c:\users\shrey\appdata\local\programs\python\python38-32\lib\site-packages\dask\dataframe\core.py:4681: UserWarning: 
You did not provide metadata, so Dask is running your function on a small dataset to guess output types. It is possible that Dask will guess incorrectly.
To provide an explicit output types or to silence this message, please provide the `meta=` keyword, as described in the map or apply function that you are using.
  Before: .apply(func)
  After:  .apply(func, meta=(None, 'bool'))

  warnings.warn(meta_warning(meta))


In [12]:
def checkstl(row):
    if row["event_type"] == "turnover":
        return "steal" in row["event_description"]
    else:
        return False
    
pbp_data2["STLA"] =pbp_data2.apply(checkstl,axis=1)

def checkblk(row):
    if row["event_type"] in ["twopointmiss","threepointmiss"]:
        return "block" in row["event_description"]
    else:
        return False
pbp_data2["BLKA"] = pbp_data2.apply(checkblk,axis=1)


In [13]:
pbp_data2.head()

game_id  \
19141  063879c7-2bae-473f-aa3f-8a68f444bb73   
19142  063879c7-2bae-473f-aa3f-8a68f444bb73   
19143  063879c7-2bae-473f-aa3f-8a68f444bb73   
19145  063879c7-2bae-473f-aa3f-8a68f444bb73   
19150  063879c7-2bae-473f-aa3f-8a68f444bb73   

                                    away_id  \
19141  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19142  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19143  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19145  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19150  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   

                                    home_id  period  \
19141  532d3874-b4b3-4c5c-acc6-749a6db26c8f       1   
19142  532d3874-b4b3-4c5c-acc6-749a6db26c8f       1   
19143  532d3874-b4b3-4c5c-acc6-749a6db26c8f       1   
19145  532d3874-b4b3-4c5c-acc6-749a6db26c8f       1   
19150  532d3874-b4b3-4c5c-acc6-749a6db26c8f       1   

                                    team_id  \
19141  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19142  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19143  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19145  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   
19150  9c7f3b90-ec9f-4a30-9ade-e0bcb8c8835e   

                           event_description     event_type    2PA    2PM  \
19141      Omar Richard turnover (traveling)       turnover  False  False   
19142  Omar Richard misses free throw 1 of 2  freethrowmiss  False  False   
19143    Jay Mayernik misses two point layup   twopointmiss   True  False   
19145     Jay Mayernik makes two point layup   twopointmade   True   True   
19150    Javonte Byrd misses two point layup   twopointmiss   True  False   

         3PA    3PM    FTA    FTM    TRB     TO   Foul  Flagrant  Ejection  \
19141  False  False  False  False  False   True  False     False     False   
19142  False  False   True  False  False  False  False     False     False   
19143  False  False  False  False  False  False  False     False     False   
19145  False  False  False  False  False  False  False     False     False   
19150  False  False  False  False  False  False  False     False     False   

         AST   STLA   BLKA  
19141  False  False  False  
19142  False  False  False  
19143  False  False  False  
19145  False  False  False  
19150  False  False  False

In [14]:
pbp_data2[(pbp_data2["BLKA"])].head()

game_id  \
19956  054771c4-3908-4486-b46a-104d50135101   
20067  5be9a30e-3582-465d-b19e-5388eddbacd5   
20126  63d257d7-4865-49d1-afd1-fd4ca560bbd5   
20137  679a305f-2359-4e0f-97ca-3d886ca3d1c3   
20178  7bee62f8-1a9f-4ab9-896c-9200ef45eea8   

                                    away_id  \
19956  c10544de-e3bd-4776-ba2e-83df8c017fd1   
20067  0d8a328f-20ce-410b-bed1-15fc01308aaf   
20126  c10544de-e3bd-4776-ba2e-83df8c017fd1   
20137  b827dbdf-230f-4916-9703-3bb9004e26eb   
20178  06d15d35-4955-4fdd-83d9-32d24dbd795b   

                                    home_id  period  \
19956  4383eb6a-7fd8-4ff2-94c5-43c933121e88       1   
20067  3a000455-de7c-4ca8-880e-abdce7f21da9       1   
20126  06d15d35-4955-4fdd-83d9-32d24dbd795b       1   
20137  4fbebf0a-e117-4a0c-8f15-c247535a2a1b       1   
20178  fae4855b-1b64-4b40-a632-9ed345e1e952       1   

                                    team_id  \
19956  4383eb6a-7fd8-4ff2-94c5-43c933121e88   
20067  0d8a328f-20ce-410b-bed1-15fc01308aaf   
20126  06d15d35-4955-4fdd-83d9-32d24dbd795b   
20137  4fbebf0a-e117-4a0c-8f15-c247535a2a1b   
20178  fae4855b-1b64-4b40-a632-9ed345e1e952   

                                       event_description    event_type   2PA  \
19956  Jarrod Uthoff blocks JayVaughn Pinkston's two ...  twopointmiss  True   
20067     D.J. Haley blocks Myles Davis's two point shot  twopointmiss  True   
20126   Aaron White blocks Cedrick Lang's two point shot  twopointmiss  True   
20137  Robert Hubbs III blocks Devin Thomas's two poi...  twopointmiss  True   
20178  John Bohannon blocks Tarik Black's two point shot  twopointmiss  True   

         2PM    3PA    3PM    FTA    FTM    TRB     TO   Foul  Flagrant  \
19956  False  False  False  False  False  False  False  False     False   
20067  False  False  False  False  False  False  False  False     False   
20126  False  False  False  False  False  False  False  False     False   
20137  False  False  False  False  False  False  False  False     False   
20178  False  False  False  False  False  False  False  False     False   

       Ejection    AST   STLA  BLKA  
19956     False  False  False  True  
20067     False  False  False  True  
20126     False  False  False  True  
20137     False  False  False  True  
20178     False  False  False  True

In [15]:
pbp_data3 = pbp_data2.groupby(["game_id","team_id"]).agg({'2PA':'sum','2PM':'sum','3PA':'sum','3PM':'sum','FTA':'sum',\
                                                         'FTM':'sum','TRB':'sum','TO':'sum','Foul':'sum','Flagrant':'sum',\
                                                         'Ejection':'sum','AST':'sum','STLA':'sum','BLKA':'sum'})

In [16]:
agg_data = pbp_data3.compute()

In [17]:
#agg_data["PTS"] = 2*agg_data["2PM"]+3*agg_data["3PM"]+agg_data["FTM"]

In [18]:
display(agg_data)

2PA  \
game_id                              team_id                                     
000872e5-f02a-4b64-ac73-b6b1a7ad10ec 4f4b0771-994c-4126-822d-7525aaa00f65   17   
                                     912f8837-1d81-4ef9-a576-a21f271d4c64   15   
000918c3-b8bf-472a-9a12-94a1984700eb 1551b3a0-6d10-4ffa-8dfa-73b56f004553   25   
                                     b795ddbc-baab-4499-8803-52e8608520ab   19   
000b3698-3ce9-44bd-954b-65703a2c6ef1 4f4b0771-994c-4126-822d-7525aaa00f65   22   
...                                                                        ...   
daec9de3-4a8a-4125-8978-a38e1fd18264 dfe0d93f-94a5-47fb-b7aa-f74786e09acb   22   
db626521-110e-443b-83a8-00ae1aaa5a28 61a3908a-7492-4b6f-809e-12c61976bb0a   18   
                                     d203f38a-a166-4258-bca2-e161b591ecfb   18   
f1063e80-23c7-486b-9a5e-faa52beb2d83 4383eb6a-7fd8-4ff2-94c5-43c933121e88   18   
                                     bdc2561d-f603-4fab-a262-f1d2af462277   15   

                                                                           2PM  \
game_id                              team_id                                     
000872e5-f02a-4b64-ac73-b6b1a7ad10ec 4f4b0771-994c-4126-822d-7525aaa00f65    7   
                                     912f8837-1d81-4ef9-a576-a21f271d4c64    3   
000918c3-b8bf-472a-9a12-94a1984700eb 1551b3a0-6d10-4ffa-8dfa-73b56f004553   11   
                                     b795ddbc-baab-4499-8803-52e8608520ab    9   
000b3698-3ce9-44bd-954b-65703a2c6ef1 4f4b0771-994c-4126-822d-7525aaa00f65    8   
...                                                                        ...   
daec9de3-4a8a-4125-8978-a38e1fd18264 dfe0d93f-94a5-47fb-b7aa-f74786e09acb    5   
db626521-110e-443b-83a8-00ae1aaa5a28 61a3908a-7492-4b6f-809e-12c61976bb0a   11   
                                     d203f38a-a166-4258-bca2-e161b591ecfb    8   
f1063e80-23c7-486b-9a5e-faa52beb2d83 4383eb6a-7fd8-4ff2-94c5-43c933121e88   10   
                                     bdc2561d-f603-4fab-a262-f1d2af462277    9   

                                                                           3PA  \
game_id                              team_id                                     
000872e5-f02a-4b64-ac73-b6b1a7ad10ec 4f4b0771-994c-4126-822d-7525aaa00f65    6   
                                     912f8837-1d81-4ef9-a576-a21f271d4c64   16   
000918c3-b8bf-472a-9a12-94a1984700eb 1551b3a0-6d10-4ffa-8dfa-73b56f004553    4   
                                     b795ddbc-baab-4499-8803-52e8608520ab    8   
000b3698-3ce9-44bd-954b-65703a2c6ef1 4f4b0771-994c-4126-822d-7525aaa00f65    9   
...                                                                        ...   
daec9de3-4a8a-4125-8978-a38e1fd18264 dfe0d93f-94a5-47fb-b7aa-f74786e09acb   10   
db626521-110e-443b-83a8-00ae1aaa5a28 61a3908a-7492-4b6f-809e-12c61976bb0a    9   
                                     d203f38a-a166-4258-bca2-e161b591ecfb    9   
f1063e80-23c7-486b-9a5e-faa52beb2d83 4383eb6a-7fd8-4ff2-94c5-43c933121e88   13   
                                     bdc2561d-f603-4fab-a262-f1d2af462277   13   

                                                                           3PM  \
game_id                              team_id                                     
000872e5-f02a-4b64-ac73-b6b1a7ad10ec 4f4b0771-994c-4126-822d-7525aaa00f65    1   
                                     912f8837-1d81-4ef9-a576-a21f271d4c64    7   
000918c3-b8bf-472a-9a12-94a1984700eb 1551b3a0-6d10-4ffa-8dfa-73b56f004553    3   
                                     b795ddbc-baab-4499-8803-52e8608520ab    2   
000b3698-3ce9-44bd-954b-65703a2c6ef1 4f4b0771-994c-4126-822d-7525aaa00f65    1   
...                                                                        ...   
daec9de3-4a8a-4125-8978-a38e1fd18264 dfe0d93f-94a5-47fb-b7aa-f74786e09acb    3   
db626521-110e-443b-83a8-00ae1aaa5a28 61a3908a-7492-4b6f-809e-12c61976bb0a    4   
                                     d203f38a-a166-425

# Merging aggregated first half data to game data:
Plan: 
1) Compute pandas dataframe g_data
2) Merge agg_data to g_data using game_id and team_id to game_id and h_id, prefix with h
3) Merge agg_data to g_data using game_id and team_id to game_id and a_id, prefix with a

In [19]:
g_data = games_data.compute()
display(g_data)



game_id  season  status  \
0      b4451a02-26c5-4005-9ac8-b06c1f71e661    2015  closed   
1      b2f579ca-9eff-4b2b-a747-81169399c2e8    2015  closed   
2      571be71c-a5bf-446e-bf21-30eb6c54ac5e    2015  closed   
3      d6617923-0b23-49e4-af9b-9e4d0243e45c    2015  closed   
4      ffb463a4-dd3c-4ed9-b503-311b95ef0295    2015  closed   
...                                     ...     ...     ...   
29800  19be97d9-1756-41ac-a00f-e08c3ea5998a    2016  closed   
29801  ff822d88-b370-429a-bc3c-dcd7e45b6560    2016  closed   
29802  c1f96ff1-b0c2-49eb-9192-803bab3fe1ae    2016  closed   
29803  3850e646-a7b2-49f1-9446-407249f9e64a    2017  closed   
29804  a91d6bb6-0ec1-43b8-9d60-3d07a732982a    2017  closed   

                coverage  neutral_site scheduled_date  \
0                   full           NaN     2015-11-24   
1                   full           NaN     2015-11-24   
2                   full           NaN     2015-11-25   
3                   full           NaN     2015-12-19   
4                   full           NaN     2015-12-20   
...                  ...           ...            ...   
29800  extended_boxscore           1.0     2016-12-23   
29801  extended_boxscore           1.0     2016-12-22   
29802  extended_boxscore           1.0     2016-12-23   
29803  extended_boxscore           1.0     2017-12-23   
29804  extended_boxscore           1.0     2017-11-25   

                      gametime conference_game tournament tournament_type  \
0      2015-11-24 21:30:00 UTC             NaN        NaN             NaN   
1      2015-11-24 02:00:00 UTC             NaN        NaN             NaN   
2      2015-11-25 19:30:00 UTC             NaN        NaN             NaN   
3      2015-12-19 04:00:00 UTC             NaN        NaN             NaN   
4      2015-12-20 04:00:00 UTC             NaN        NaN             NaN   
...                        ...             ...        ...             ...   
29800  2016-12-23 20:00:00 UTC           False        NaN             NaN   
29801  2016-12-22 22:30:00 UTC           False        NaN             NaN   
29802  2016-12-23 01:30:00 UTC           False        NaN             NaN   
29803  2017-12-23 01:30:00 UTC           False        NaN             NaN   
29804  2017-11-25 03:30:00 UTC           False        NaN             NaN   

      tournament_round tournament_game_no  attendance  lead_changes  \
0                  NaN                NaN      2400.0           3.0   
1                  NaN                NaN      2400.0           1.0   
2                  NaN                NaN      2400.0           2.0   
3                  NaN                NaN      8032.0           9.0   
4                  NaN                NaN      8555.0           1.0   
...                ...                ...         ...           ...   
29800              NaN                NaN         0.0           0.0   
29801              NaN                NaN      4148.0           1.0   
29802              NaN                NaN         NaN           4.0   
29803              NaN                NaN         NaN           9.0   
29804              NaN                NaN      3325.0           2.0   

       times_tied  periods                      possession_arrow  \
0             2.0      2.0  68a3227f-677f-43b0-9a3a-cad79d0df9e2   
1             0.0      2.0  fae4855b-1b64-4b40-a632-9ed345e1e952   
2             0.0      2.0  ef13a371-76ed-409c-9aa6-35135183e170   
3             1.0      2.0  532d3874-b4b3-4c5c-acc6-749a6db26c8f   
4             3.0      2.0  2959bd24-7007-41ae-a3a3-abdf26888cfc   
...           ...      ...                                   ...   
29800         0.0      2.0                                   NaN   
29801         3.0      2.0                                   NaN   
29802         5.0      2.0                                   NaN   
29803         3.0      2.0                                   NaN   
29804         4.0      2.0                                   NaN   


In [20]:
# Margin of Victory column
games_data['MOV'] = games_data['h_points_game']-games_data['a_points_game']
print("--------")
display(games_data['MOV'])
print("--------")
display(games_data.compute()['MOV'])

--------


Dask Series Structure:
npartitions=1
    int64
      ...
Name: MOV, dtype: int64
Dask Name: getitem, 6 tasks

--------


0       -20
1       -51
2        -7
3        13
4         5
         ..
29800    16
29801    -8
29802   -14
29803     2
29804    14
Name: MOV, Length: 29805, dtype: int64

In [21]:
feature_subset = ['game_id','h_id','a_id','season','conference_game','tournament','tournament_type',\
                 'tournament_round','tournament_game_no','attendance','venue_id','venue_city','venue_state',\
                 'venue_address','venue_zip','venue_capacity','MOV',\
                 'h_market','h_conf_id','h_conf_name','h_division_alias','h_points_game',\
                 'a_market','a_conf_id','a_conf_name','a_division_alias','a_points_game']

In [22]:
g_data = games_data[feature_subset].compute()

In [23]:
g_data2 = g_data.merge(agg_data.add_prefix('h_'),how='inner',left_on=['game_id','h_id'],right_on=['game_id','team_id'])
display(g_data2)

game_id  \
0      b4451a02-26c5-4005-9ac8-b06c1f71e661   
1      b2f579ca-9eff-4b2b-a747-81169399c2e8   
2      571be71c-a5bf-446e-bf21-30eb6c54ac5e   
3      d6617923-0b23-49e4-af9b-9e4d0243e45c   
4      ffb463a4-dd3c-4ed9-b503-311b95ef0295   
...                                     ...   
11158  9dfe8c82-8d85-42f7-b88d-5a3e2849c74c   
11159  79e583e6-fffe-460e-821b-2157affad34f   
11160  346a418b-995d-4a81-9d02-e567d6265878   
11161  7258d3e6-1b7e-4139-b4fb-7f469dbc4c39   
11162  ba19db74-4640-499c-9417-dd8b7f144ea3   

                                       h_id  \
0      ef13a371-76ed-409c-9aa6-35135183e170   
1      ef13a371-76ed-409c-9aa6-35135183e170   
2      ef13a371-76ed-409c-9aa6-35135183e170   
3      532d3874-b4b3-4c5c-acc6-749a6db26c8f   
4      532d3874-b4b3-4c5c-acc6-749a6db26c8f   
...                                     ...   
11158  bdb7d7a4-45f8-4bf3-ab85-15488c451494   
11159  d52c3640-069c-4554-982e-e6537c8044f1   
11160  fea46ac5-6dad-43cd-a770-75554dbcc118   
11161  820c8f26-cf11-4997-b2e2-19f47bd2f72f   
11162  7e100f63-0b32-49f6-a954-f5b7c8cf48ad   

                                       a_id  season conference_game  \
0      68a3227f-677f-43b0-9a3a-cad79d0df9e2    2015             NaN   
1      fae4855b-1b64-4b40-a632-9ed345e1e952    2015             NaN   
2      c1f4aae1-aa16-4095-aeab-10e5c2a1236a    2015             NaN   
3      c009914b-3303-4dee-b915-978aa48a31d0    2015             NaN   
4      2959bd24-7007-41ae-a3a3-abdf26888cfc    2015             NaN   
...                                     ...     ...             ...   
11158  9b166a3f-e64b-4825-bb6b-92c6f0418263    2016           False   
11159  0d8a328f-20ce-410b-bed1-15fc01308aaf    2017           False   
11160  7cdfcf92-7fe7-46f1-9b66-6912114182e6    2017           False   
11161  92456e1e-f48c-4385-96ab-14cb27d18726    2016           False   
11162  92456e1e-f48c-4385-96ab-14cb27d18726    2017           False   

       tournament   tournament_type tournament_round tournament_game_no  \
0             NaN               NaN              NaN                NaN   
1             NaN               NaN              NaN                NaN   
2             NaN               NaN              NaN                NaN   
3             NaN               NaN              NaN                NaN   
4             NaN               NaN              NaN                NaN   
...           ...               ...              ...                ...   
11158         NaN               NaN              NaN                NaN   
11159         NaN               NaN              NaN                NaN   
11160         NaN               NaN              NaN                NaN   
11161  Conference  Western Athletic   Quarterfinal 3                NaN   
11162  Conference  Western Athletic   Quarterfinal 4                NaN   

       attendance                              venue_id venue_city  \
0          2400.0  c69e13a7-4637-4b0e-9ca8-043ac5738a9d       Maui   
1          2400.0  c69e13a7-4637-4b0e-9ca8-043ac5738a9d       Maui   
2          2400.0  c69e13a7-4637-4b0e-9ca8-043ac5738a9d       Maui   
3          8032.0  1d1f74a2-7b35-56f0-8cbd-552c51cb2c14   Portland   
4          8555.0  1d1f74a2-7b35-56f0-8cbd-552c51cb2c14   Portland   
...           ...                                   ...        ...   
11158         NaN  7b49816c-cac2-40d5-97bc-7c8c0935039d  Las Vegas   
11159         NaN  7b49816c-cac2-40d5-97bc-7c8c0935039d  Las Vegas   
11160         0.0  7b49816c-cac2-40d5-97bc-7c8c0935039d  Las Vegas   
11161      1854.0  7b49816c-cac2-40d5-97bc-7c8c0935039d  Las Vegas   
11162      1349.0  7b49816c-cac2-40d5-97bc-7c8c0935039d  Las Vegas   

      venue_state          venue_address venue_zip  venue_capacity  MOV  \
0              HI  1840 Honoapiilani Hwy     96761          2400.0  -20   
1              HI  1840 Honoapiilani Hwy     96761          2400.0  -51   
2              HI  1840 Honoapiilani Hwy     96761          2400.0   -7   
3          

In [24]:
g_data2.columns

Index(['game_id', 'h_id', 'a_id', 'season', 'conference_game', 'tournament',
       'tournament_type', 'tournament_round', 'tournament_game_no',
       'attendance', 'venue_id', 'venue_city', 'venue_state', 'venue_address',
       'venue_zip', 'venue_capacity', 'MOV', 'h_market', 'h_conf_id',
       'h_conf_name', 'h_division_alias', 'h_points_game', 'a_market',
       'a_conf_id', 'a_conf_name', 'a_division_alias', 'a_points_game',
       'h_2PA', 'h_2PM', 'h_3PA', 'h_3PM', 'h_FTA', 'h_FTM', 'h_TRB', 'h_TO',
       'h_Foul', 'h_Flagrant', 'h_Ejection', 'h_AST', 'h_STLA', 'h_BLKA'],
      dtype='object')

In [25]:
g_data3 = g_data2.merge(agg_data.add_prefix('a_'),how='inner',left_on=['game_id','a_id'],right_on=['game_id','team_id'])

In [26]:
display(g_data3)

game_id  \
0      b4451a02-26c5-4005-9ac8-b06c1f71e661   
1      b2f579ca-9eff-4b2b-a747-81169399c2e8   
2      571be71c-a5bf-446e-bf21-30eb6c54ac5e   
3      d6617923-0b23-49e4-af9b-9e4d0243e45c   
4      ffb463a4-dd3c-4ed9-b503-311b95ef0295   
...                                     ...   
11158  9dfe8c82-8d85-42f7-b88d-5a3e2849c74c   
11159  79e583e6-fffe-460e-821b-2157affad34f   
11160  346a418b-995d-4a81-9d02-e567d6265878   
11161  7258d3e6-1b7e-4139-b4fb-7f469dbc4c39   
11162  ba19db74-4640-499c-9417-dd8b7f144ea3   

                                       h_id  \
0      ef13a371-76ed-409c-9aa6-35135183e170   
1      ef13a371-76ed-409c-9aa6-35135183e170   
2      ef13a371-76ed-409c-9aa6-35135183e170   
3      532d3874-b4b3-4c5c-acc6-749a6db26c8f   
4      532d3874-b4b3-4c5c-acc6-749a6db26c8f   
...                                     ...   
11158  bdb7d7a4-45f8-4bf3-ab85-15488c451494   
11159  d52c3640-069c-4554-982e-e6537c8044f1   
11160  fea46ac5-6dad-43cd-a770-75554dbcc118   
11161  820c8f26-cf11-4997-b2e2-19f47bd2f72f   
11162  7e100f63-0b32-49f6-a954-f5b7c8cf48ad   

                                       a_id  season conference_game  \
0      68a3227f-677f-43b0-9a3a-cad79d0df9e2    2015             NaN   
1      fae4855b-1b64-4b40-a632-9ed345e1e952    2015             NaN   
2      c1f4aae1-aa16-4095-aeab-10e5c2a1236a    2015             NaN   
3      c009914b-3303-4dee-b915-978aa48a31d0    2015             NaN   
4      2959bd24-7007-41ae-a3a3-abdf26888cfc    2015             NaN   
...                                     ...     ...             ...   
11158  9b166a3f-e64b-4825-bb6b-92c6f0418263    2016           False   
11159  0d8a328f-20ce-410b-bed1-15fc01308aaf    2017           False   
11160  7cdfcf92-7fe7-46f1-9b66-6912114182e6    2017           False   
11161  92456e1e-f48c-4385-96ab-14cb27d18726    2016           False   
11162  92456e1e-f48c-4385-96ab-14cb27d18726    2017           False   

       tournament   tournament_type tournament_round tournament_game_no  \
0             NaN               NaN              NaN                NaN   
1             NaN               NaN              NaN                NaN   
2             NaN               NaN              NaN                NaN   
3             NaN               NaN              NaN                NaN   
4             NaN               NaN              NaN                NaN   
...           ...               ...              ...                ...   
11158         NaN               NaN              NaN                NaN   
11159         NaN               NaN              NaN                NaN   
11160         NaN               NaN              NaN                NaN   
11161  Conference  Western Athletic   Quarterfinal 3                NaN   
11162  Conference  Western Athletic   Quarterfinal 4                NaN   

       attendance                              venue_id venue_city  \
0          2400.0  c69e13a7-4637-4b0e-9ca8-043ac5738a9d       Maui   
1          2400.0  c69e13a7-4637-4b0e-9ca8-043ac5738a9d       Maui   
2          2400.0  c69e13a7-4637-4b0e-9ca8-043ac5738a9d       Maui   
3          8032.0  1d1f74a2-7b35-56f0-8cbd-552c51cb2c14   Portland   
4          8555.0  1d1f74a2-7b35-56f0-8cbd-552c51cb2c14   Portland   
...           ...                                   ...        ...   
11158         NaN  7b49816c-cac2-40d5-97bc-7c8c0935039d  Las Vegas   
11159         NaN  7b49816c-cac2-40d5-97bc-7c8c0935039d  Las Vegas   
11160         0.0  7b49816c-cac2-40d5-97bc-7c8c0935039d  Las Vegas   
11161      1854.0  7b49816c-cac2-40d5-97bc-7c8c0935039d  Las Vegas   
11162      1349.0  7b49816c-cac2-40d5-97bc-7c8c0935039d  Las Vegas   

      venue_state          venue_address venue_zip  venue_capacity  MOV  \
0              HI  1840 Honoapiilani Hwy     96761          2400.0  -20   
1              HI  1840 Honoapiilani Hwy     96761          2400.0  -51   
2              HI  1840 Honoapiilani Hwy     96761          2400.0   -7   
3          

In [27]:
type(g_data3)

pandas.core.frame.DataFrame

In [28]:
g_data4 = g_data3.set_index(['game_id'],verify_integrity=True)
display(g_data4)

h_id  \
game_id                                                                      
b4451a02-26c5-4005-9ac8-b06c1f71e661  ef13a371-76ed-409c-9aa6-35135183e170   
b2f579ca-9eff-4b2b-a747-81169399c2e8  ef13a371-76ed-409c-9aa6-35135183e170   
571be71c-a5bf-446e-bf21-30eb6c54ac5e  ef13a371-76ed-409c-9aa6-35135183e170   
d6617923-0b23-49e4-af9b-9e4d0243e45c  532d3874-b4b3-4c5c-acc6-749a6db26c8f   
ffb463a4-dd3c-4ed9-b503-311b95ef0295  532d3874-b4b3-4c5c-acc6-749a6db26c8f   
...                                                                    ...   
9dfe8c82-8d85-42f7-b88d-5a3e2849c74c  bdb7d7a4-45f8-4bf3-ab85-15488c451494   
79e583e6-fffe-460e-821b-2157affad34f  d52c3640-069c-4554-982e-e6537c8044f1   
346a418b-995d-4a81-9d02-e567d6265878  fea46ac5-6dad-43cd-a770-75554dbcc118   
7258d3e6-1b7e-4139-b4fb-7f469dbc4c39  820c8f26-cf11-4997-b2e2-19f47bd2f72f   
ba19db74-4640-499c-9417-dd8b7f144ea3  7e100f63-0b32-49f6-a954-f5b7c8cf48ad   

                                                                      a_id  \
game_id                                                                      
b4451a02-26c5-4005-9ac8-b06c1f71e661  68a3227f-677f-43b0-9a3a-cad79d0df9e2   
b2f579ca-9eff-4b2b-a747-81169399c2e8  fae4855b-1b64-4b40-a632-9ed345e1e952   
571be71c-a5bf-446e-bf21-30eb6c54ac5e  c1f4aae1-aa16-4095-aeab-10e5c2a1236a   
d6617923-0b23-49e4-af9b-9e4d0243e45c  c009914b-3303-4dee-b915-978aa48a31d0   
ffb463a4-dd3c-4ed9-b503-311b95ef0295  2959bd24-7007-41ae-a3a3-abdf26888cfc   
...                                                                    ...   
9dfe8c82-8d85-42f7-b88d-5a3e2849c74c  9b166a3f-e64b-4825-bb6b-92c6f0418263   
79e583e6-fffe-460e-821b-2157affad34f  0d8a328f-20ce-410b-bed1-15fc01308aaf   
346a418b-995d-4a81-9d02-e567d6265878  7cdfcf92-7fe7-46f1-9b66-6912114182e6   
7258d3e6-1b7e-4139-b4fb-7f469dbc4c39  92456e1e-f48c-4385-96ab-14cb27d18726   
ba19db74-4640-499c-9417-dd8b7f144ea3  92456e1e-f48c-4385-96ab-14cb27d18726   

                                      season conference_game  tournament  \
game_id                                                                    
b4451a02-26c5-4005-9ac8-b06c1f71e661    2015             NaN         NaN   
b2f579ca-9eff-4b2b-a747-81169399c2e8    2015             NaN         NaN   
571be71c-a5bf-446e-bf21-30eb6c54ac5e    2015             NaN         NaN   
d6617923-0b23-49e4-af9b-9e4d0243e45c    2015             NaN         NaN   
ffb463a4-dd3c-4ed9-b503-311b95ef0295    2015             NaN         NaN   
...                                      ...             ...         ...   
9dfe8c82-8d85-42f7-b88d-5a3e2849c74c    2016           False         NaN   
79e583e6-fffe-460e-821b-2157affad34f    2017           False         NaN   
346a418b-995d-4a81-9d02-e567d6265878    2017           False         NaN   
7258d3e6-1b7e-4139-b4fb-7f469dbc4c39    2016           False  Conference   
ba19db74-4640-499c-9417-dd8b7f144ea3    2017           False  Conference   

                                       tournament_type tournament_round  \
game_id                                                                   
b4451a02-26c5-4005-9ac8-b06c1f71e661               NaN              NaN   
b2f579ca-9eff-4b2b-a747-81169399c2e8               NaN              NaN   
571be71c-a5bf-446e-bf21-30eb6c54ac5e               NaN              NaN   
d6617923-0b23-49e4-af9b-9e4d0243e45c               NaN              NaN   
ffb463a4-dd3c-4ed9-b503-311b95ef0295               NaN              NaN   
...                                                ...              ...   
9dfe8c82-8d85-42f7-b88d-5a3e2849c74c               NaN              NaN   
79e583e6-fffe-460e-821b-2157affad34f               NaN              NaN   
346a418b-995d-4a81-9d02-e567d6265878               NaN              NaN   
7258d3e6-1b7e-4139-b4fb-7f469dbc4c39  Western Athletic   Quarterfinal 3   
ba19db74-4640-499c-9417-dd8b7f144ea3  Western Athletic   Quarterfinal 4   

                                     tournament_game_no  attendance  \
game

In [29]:
df = g_data4.loc[(g_data4['h_division_alias']=='D1')&(g_data4['a_division_alias']=='D1')]

In [30]:
display(df)

h_id  \
game_id                                                                      
d6617923-0b23-49e4-af9b-9e4d0243e45c  532d3874-b4b3-4c5c-acc6-749a6db26c8f   
ffb463a4-dd3c-4ed9-b503-311b95ef0295  532d3874-b4b3-4c5c-acc6-749a6db26c8f   
1063177e-e168-4055-bdbf-a7fd1e33f398  9fccbf28-2858-4263-821c-fdefb3c7efa3   
60b9ce90-41cb-4158-8038-1f9f80b374a5  532d3874-b4b3-4c5c-acc6-749a6db26c8f   
267af1b7-9c86-4561-bf63-7a379cdaae6d  9b166a3f-e64b-4825-bb6b-92c6f0418263   
...                                                                    ...   
9dfe8c82-8d85-42f7-b88d-5a3e2849c74c  bdb7d7a4-45f8-4bf3-ab85-15488c451494   
79e583e6-fffe-460e-821b-2157affad34f  d52c3640-069c-4554-982e-e6537c8044f1   
346a418b-995d-4a81-9d02-e567d6265878  fea46ac5-6dad-43cd-a770-75554dbcc118   
7258d3e6-1b7e-4139-b4fb-7f469dbc4c39  820c8f26-cf11-4997-b2e2-19f47bd2f72f   
ba19db74-4640-499c-9417-dd8b7f144ea3  7e100f63-0b32-49f6-a954-f5b7c8cf48ad   

                                                                      a_id  \
game_id                                                                      
d6617923-0b23-49e4-af9b-9e4d0243e45c  c009914b-3303-4dee-b915-978aa48a31d0   
ffb463a4-dd3c-4ed9-b503-311b95ef0295  2959bd24-7007-41ae-a3a3-abdf26888cfc   
1063177e-e168-4055-bdbf-a7fd1e33f398  efba5350-79bc-47aa-a189-db177b95b491   
60b9ce90-41cb-4158-8038-1f9f80b374a5  c1c1e6df-a383-4fbd-ba7b-32d4f9ef9518   
267af1b7-9c86-4561-bf63-7a379cdaae6d  f38b58de-3273-4723-a78b-2f918e9aa2d5   
...                                                                    ...   
9dfe8c82-8d85-42f7-b88d-5a3e2849c74c  9b166a3f-e64b-4825-bb6b-92c6f0418263   
79e583e6-fffe-460e-821b-2157affad34f  0d8a328f-20ce-410b-bed1-15fc01308aaf   
346a418b-995d-4a81-9d02-e567d6265878  7cdfcf92-7fe7-46f1-9b66-6912114182e6   
7258d3e6-1b7e-4139-b4fb-7f469dbc4c39  92456e1e-f48c-4385-96ab-14cb27d18726   
ba19db74-4640-499c-9417-dd8b7f144ea3  92456e1e-f48c-4385-96ab-14cb27d18726   

                                      season conference_game  tournament  \
game_id                                                                    
d6617923-0b23-49e4-af9b-9e4d0243e45c    2015             NaN         NaN   
ffb463a4-dd3c-4ed9-b503-311b95ef0295    2015             NaN         NaN   
1063177e-e168-4055-bdbf-a7fd1e33f398    2015             NaN        NCAA   
60b9ce90-41cb-4158-8038-1f9f80b374a5    2015             NaN        NCAA   
267af1b7-9c86-4561-bf63-7a379cdaae6d    2015             NaN        NCAA   
...                                      ...             ...         ...   
9dfe8c82-8d85-42f7-b88d-5a3e2849c74c    2016           False         NaN   
79e583e6-fffe-460e-821b-2157affad34f    2017           False         NaN   
346a418b-995d-4a81-9d02-e567d6265878    2017           False         NaN   
7258d3e6-1b7e-4139-b4fb-7f469dbc4c39    2016           False  Conference   
ba19db74-4640-499c-9417-dd8b7f144ea3    2017           False  Conference   

                                       tournament_type tournament_round  \
game_id                                                                   
d6617923-0b23-49e4-af9b-9e4d0243e45c               NaN              NaN   
ffb463a4-dd3c-4ed9-b503-311b95ef0295               NaN              NaN   
1063177e-e168-4055-bdbf-a7fd1e33f398    South Regional      First Round   
60b9ce90-41cb-4158-8038-1f9f80b374a5     West Regional      First Round   
267af1b7-9c86-4561-bf63-7a379cdaae6d    South Regional      First Round   
...                                                ...              ...   
9dfe8c82-8d85-42f7-b88d-5a3e2849c74c               NaN              NaN   
79e583e6-fffe-460e-821b-2157affad34f               NaN              NaN   
346a418b-995d-4a81-9d02-e567d6265878               NaN              NaN   
7258d3e6-1b7e-4139-b4fb-7f469dbc4c39  Western Athletic   Quarterfinal 3   
ba19db74-4640-499c-9417-dd8b7f144ea3  Western Athletic   Quarterfinal 4   

                                     tournament_game_no  attendance  \
game

In [31]:
df.shape

(11058, 54)

In [32]:
df["season"].unique()







array([2015, 2013, 2014, 2017, 2016], dtype=int64)

In [33]:
#Checking how many games are tournament
df['tournament'].unique()

array([nan, 'NCAA', 'Conference'], dtype=object)

In [34]:
df['tournament_type'].unique()

array([nan, 'South Regional', 'West Regional', 'Midwest Regional',
       'East Regional', 'SCAR Bracket', 'Pac', 'CBI', 'Ohio Valley',
       'CIT', 'Missouri Valley', 'Horizon League', 'Valparaiso Bracket',
       'Final Four', 'Big 12', 'Sun Belt', 'Big South', 'Big Sky',
       'American Athletic', 'Southern', 'Summit League', 'Big West',
       'Vegas 16', 'Conference USA', 'Southland', 'First Four', 'MEAC',
       'ACC', 'National Championship', 'SBON Bracket', 'Atlantic Sun',
       'Monmouth Bracket', 'Patriot League', 'Mountain West',
       'Southeastern', 'Mid', 'Big Ten', 'America East', 'Northeast',
       'Colonial Athletic', 'MAAC', 'Colorado St. Bracket',
       'Old Dominion Bracket', 'Temple Bracket', 'Richmond Bracket',
       'SWAC', 'Atlantic Coast', 'SEC', 'California Bracket',
       'Illinois St Bracket', 'Iowa Bracket', 'Syracuse Bracket',
       'Southwest Athletic', 'Ivy League', 'Atlantic 10',
       'Metro Atlantic', 'NIT', 'Big East', 'Western Athletic',
 

In [57]:
client.close()

In [36]:
df.to_csv()

'game_id,h_id,a_id,season,conference_game,tournament,tournament_type,tournament_round,tournament_game_no,attendance,venue_id,venue_city,venue_state,venue_address,venue_zip,venue_capacity,MOV,h_market,h_conf_id,h_conf_name,h_division_alias,h_points_game,a_market,a_conf_id,a_conf_name,a_division_alias,a_points_game,h_2PA,h_2PM,h_3PA,h_3PM,h_FTA,h_FTM,h_TRB,h_TO,h_Foul,h_Flagrant,h_Ejection,h_AST,h_STLA,h_BLKA,a_2PA,a_2PM,a_3PA,a_3PM,a_FTA,a_FTM,a_TRB,a_TO,a_Foul,a_Flagrant,a_Ejection,a_AST,a_STLA,a_BLKA\r\nd6617923-0b23-49e4-af9b-9e4d0243e45c,532d3874-b4b3-4c5c-acc6-749a6db26c8f,c009914b-3303-4dee-b915-978aa48a31d0,2015,,,,,,8032.0,1d1f74a2-7b35-56f0-8cbd-552c51cb2c14,Portland,OR,1 Center Court,97227,19441.0,13,Oregon State,04d5255d-b2dc-43df-9fa8-d296b0f8ccd7,Pacific 12,D1,82,Cal State Fullerton,5f56da49-5d81-43c3-8652-8b8da40c907f,Big West,D1,69,19,10,14,6,9,6,24,5,3,0,0,8,1,0,12,4,16,6,13,6,18,4,5,0,0,5,1,1\r\nffb463a4-dd3c-4ed9-b503-311b95ef0295,532d3874-b4b3-4c5c-acc6-749a6db26c8f,2